# Grid Search for Bonston Housing dataset

In [1]:
# Load required libraries
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.utils.data

import numpy as np
import matplotlib.pyplot as plt
from sklearn.datasets import load_boston
from sklearn.model_selection import train_test_split

In [2]:
# Set seed
np.random.seed(42)
torch.manual_seed(42)

# Load Boston Housing dataset
boston = load_boston(return_X_y=False)

# Split into training, validation and test set
X_train, X_test, y_train, y_test = train_test_split(boston.data, boston.target, test_size=50, random_state=42)
X_train, X_val, y_train, y_val = train_test_split(X_train, y_train, test_size=40, random_state=42)

# Convert arrays to Torch tensors
X_train = torch.FloatTensor(X_train)
y_train = torch.FloatTensor(y_train).view(-1,1)
X_val = torch.FloatTensor(X_val)
y_val = torch.FloatTensor(y_val).view(-1,1)
X_test = torch.FloatTensor(X_test)
y_test = torch.FloatTensor(y_test).view(-1,1)

# Normalise the training dataset
X_train_mean = X_train.mean(0)
X_train_std = X_train.std(0)
X_train_norm = X_train.add(-1, X_train_mean) / X_train_std
y_train_mean = torch.mean(y_train)
y_train_std = torch.std(y_train)
y_train_norm = y_train.add(-1, y_train_mean) / y_train_std

# Define the data-loader
train_data = torch.utils.data.TensorDataset(X_train_norm, y_train_norm)
train_loader = torch.utils.data.DataLoader(train_data, batch_size=32, num_workers=0)
val_data = torch.utils.data.TensorDataset(X_val, y_val)
val_loader = torch.utils.data.DataLoader(val_data, batch_size=40)
test_data = torch.utils.data.TensorDataset(X_test, y_test)
test_loader = torch.utils.data.DataLoader(test_data, batch_size=50)

In [3]:
# Fully connected Feed-Forward network with 2 hidden layers and SELU activations
if torch.cuda.is_available():
    device = torch.device("cuda")
else:
    device = torch.device("cpu")

class Model(nn.Module):

    def __init__(self):
        super(Model, self).__init__()
        self.model = nn.Sequential(
                      nn.Linear(13, 50, bias=True),
                      nn.SELU(),
                      nn.Linear(50, 50, bias=True),
                      nn.SELU(),
                      nn.Linear(50, 50, bias=True),
                      nn.SELU(),
                      nn.Linear(50,1, bias=True)
                    ).to(device)


    def forward(self, x):
        x = x.view(x.size(0), -1)
        x = self.model(x)
        return x

In [4]:
# RMSE function with online computed predictive mean and std error
class evaluation(object):
    def __init__(self, val_data, n_samples, X_mean=None, X_std=None, y_mean=None, y_std=None):
        self.val_data = val_data
        self.X_mean = X_mean
        self.X_std = X_std
        self.y_mean = y_mean
        self.y_std = y_std
        self.n = 0
        self.avg_prediction = 0.
 

    def rmse(self, model):

        with torch.autograd.no_grad():
            self.n += 1
            for x, y in iter(self.val_data):
                x = x.view(x.size(0), -1)

                if (self.X_mean is not None) & (self.X_std is not None):
                    x = (x - self.X_mean).float() / self.X_std

                standard_pred = model(x)

                if (self.y_mean is not None) & (self.y_std is not None):
                    standard_pred = standard_pred * self.y_std + self.y_mean
  
                self.avg_prediction = self.avg_prediction * (self.n - 1.) / self.n + standard_pred.view(-1,1) / self.n
                error = nn.MSELoss(size_average=True)
                rmse = error(self.avg_prediction, y) ** 0.5

                return rmse

## SGLD

In [5]:
# Load required libraries
import torch
import torchvision

from torch import nn
import torch.nn.functional as F
import numpy as np

import sgld
import model

# Set seed
np.random.seed(42)
torch.manual_seed(42)


# Network hyperparameters
lambda_ = 1.
learning_rates = [7e-6, 6e-6, 5e-6, 4e-6, 3e-6, 2e-6, 1e-6, 9e-7, 8e-7]
batch_size = 32.
dataset_size= 416.
# Number of samples to draw from the posterior distribution
n_samples = 300

# Initialise result array
val_results = np.zeros((5,9))



for i in range(5):
    for j,lr in enumerate(learning_rates):
        network = Model()
        criterion = nn.MSELoss(size_average=False)
        optim = sgld.optim.sgld(network, lr, lambda_, batch_size, dataset_size)
        evaluate = evaluation(val_loader, n_samples, X_train_mean, X_train_std, y_train_mean, y_train_std)
        
        t = 1
        n = 0
        for epoch in range(2500):

            running_loss = 0
            for x, y in iter(train_loader):
                x = x.view(x.size(0), -1)

                network.zero_grad()
                output = network(x)
                loss = 0.5 * criterion(output, y)
                loss.backward()
                optim.step()



                running_loss += loss * batch_size / dataset_size

                # Sample from the posterior distribution
                if (t >= 300) & (t % 100 == 0) & (n < n_samples):
                    rmse = evaluate.rmse(network)
                    n += 1
                t += 1.
            print("lr {:.8f} - epoch {:d} - loss: {:.4f}".format(lr, epoch, running_loss))
        val_results[i,j] = rmse

/opt/anaconda/envs/Python3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))


lr 0.00000700 - epoch 0 - loss: 6.8823
lr 0.00000700 - epoch 1 - loss: 4.5868
lr 0.00000700 - epoch 2 - loss: 4.1835
lr 0.00000700 - epoch 3 - loss: 4.0197
lr 0.00000700 - epoch 4 - loss: 3.9065
lr 0.00000700 - epoch 5 - loss: 3.8586
lr 0.00000700 - epoch 6 - loss: 3.8007
lr 0.00000700 - epoch 7 - loss: 3.7828
lr 0.00000700 - epoch 8 - loss: 3.6202
lr 0.00000700 - epoch 9 - loss: 3.6837
lr 0.00000700 - epoch 10 - loss: 3.5471
lr 0.00000700 - epoch 11 - loss: 3.4739
lr 0.00000700 - epoch 12 - loss: 3.3759
lr 0.00000700 - epoch 13 - loss: 3.3808
lr 0.00000700 - epoch 14 - loss: 3.1913
lr 0.00000700 - epoch 15 - loss: 3.2351
lr 0.00000700 - epoch 16 - loss: 3.2499
lr 0.00000700 - epoch 17 - loss: 3.3553
lr 0.00000700 - epoch 18 - loss: 3.1124
lr 0.00000700 - epoch 19 - loss: 3.0649
lr 0.00000700 - epoch 20 - loss: 3.0649
lr 0.00000700 - epoch 21 - loss: 2.8663
lr 0.00000700 - epoch 22 - loss: 2.8292
lr 0.00000700 - epoch 23 - loss: 2.7724
lr 0.00000700 - epoch 24 - loss: 2.7254
lr 0.00000

/opt/anaconda/envs/Python3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='elementwise_mean' instead.
  warnings.warn(warning.format(ret))


lr 0.00000700 - epoch 26 - loss: 2.6008
lr 0.00000700 - epoch 27 - loss: 2.5144
lr 0.00000700 - epoch 28 - loss: 2.5881
lr 0.00000700 - epoch 29 - loss: 2.5785
lr 0.00000700 - epoch 30 - loss: 2.4441
lr 0.00000700 - epoch 31 - loss: 2.4188
lr 0.00000700 - epoch 32 - loss: 2.4749
lr 0.00000700 - epoch 33 - loss: 2.3719
lr 0.00000700 - epoch 34 - loss: 2.3782
lr 0.00000700 - epoch 35 - loss: 2.2513
lr 0.00000700 - epoch 36 - loss: 2.3465
lr 0.00000700 - epoch 37 - loss: 2.2663
lr 0.00000700 - epoch 38 - loss: 2.1895
lr 0.00000700 - epoch 39 - loss: 2.2812
lr 0.00000700 - epoch 40 - loss: 2.1556
lr 0.00000700 - epoch 41 - loss: 2.2099
lr 0.00000700 - epoch 42 - loss: 2.1995
lr 0.00000700 - epoch 43 - loss: 2.1574
lr 0.00000700 - epoch 44 - loss: 2.2462
lr 0.00000700 - epoch 45 - loss: 2.1836
lr 0.00000700 - epoch 46 - loss: 2.1846
lr 0.00000700 - epoch 47 - loss: 2.1201
lr 0.00000700 - epoch 48 - loss: 2.1004
lr 0.00000700 - epoch 49 - loss: 2.1987
lr 0.00000700 - epoch 50 - loss: 2.1807


lr 0.00000700 - epoch 231 - loss: 0.9731
lr 0.00000700 - epoch 232 - loss: 0.8827
lr 0.00000700 - epoch 233 - loss: 0.8663
lr 0.00000700 - epoch 234 - loss: 0.8593
lr 0.00000700 - epoch 235 - loss: 0.9210
lr 0.00000700 - epoch 236 - loss: 0.8906
lr 0.00000700 - epoch 237 - loss: 0.8721
lr 0.00000700 - epoch 238 - loss: 0.8244
lr 0.00000700 - epoch 239 - loss: 0.7991
lr 0.00000700 - epoch 240 - loss: 0.8638
lr 0.00000700 - epoch 241 - loss: 0.8786
lr 0.00000700 - epoch 242 - loss: 0.8246
lr 0.00000700 - epoch 243 - loss: 0.8594
lr 0.00000700 - epoch 244 - loss: 0.9467
lr 0.00000700 - epoch 245 - loss: 1.1095
lr 0.00000700 - epoch 246 - loss: 0.9476
lr 0.00000700 - epoch 247 - loss: 0.9217
lr 0.00000700 - epoch 248 - loss: 1.5106
lr 0.00000700 - epoch 249 - loss: 0.9197
lr 0.00000700 - epoch 250 - loss: 1.0658
lr 0.00000700 - epoch 251 - loss: 0.9120
lr 0.00000700 - epoch 252 - loss: 0.8547
lr 0.00000700 - epoch 253 - loss: 0.9144
lr 0.00000700 - epoch 254 - loss: 0.8751
lr 0.00000700 - 

...

lr 0.00000080 - epoch 1683 - loss: 0.5366
lr 0.00000080 - epoch 1684 - loss: 0.5344
lr 0.00000080 - epoch 1685 - loss: 0.5306
lr 0.00000080 - epoch 1686 - loss: 0.5326
lr 0.00000080 - epoch 1687 - loss: 0.5327
lr 0.00000080 - epoch 1688 - loss: 0.5316
lr 0.00000080 - epoch 1689 - loss: 0.5289
lr 0.00000080 - epoch 1690 - loss: 0.5259
lr 0.00000080 - epoch 1691 - loss: 0.5336
lr 0.00000080 - epoch 1692 - loss: 0.5280
lr 0.00000080 - epoch 1693 - loss: 0.5279
lr 0.00000080 - epoch 1694 - loss: 0.5225
lr 0.00000080 - epoch 1695 - loss: 0.5198
lr 0.00000080 - epoch 1696 - loss: 0.5271
lr 0.00000080 - epoch 1697 - loss: 0.5293
lr 0.00000080 - epoch 1698 - loss: 0.5282
lr 0.00000080 - epoch 1699 - loss: 0.5226
lr 0.00000080 - epoch 1700 - loss: 0.5203
lr 0.00000080 - epoch 1701 - loss: 0.5190
lr 0.00000080 - epoch 1702 - loss: 0.5236
lr 0.00000080 - epoch 1703 - loss: 0.5189
lr 0.00000080 - epoch 1704 - loss: 0.5176
lr 0.00000080 - epoch 1705 - loss: 0.5322
lr 0.00000080 - epoch 1706 - loss:

lr 0.00000080 - epoch 1880 - loss: 0.5031
lr 0.00000080 - epoch 1881 - loss: 0.5008
lr 0.00000080 - epoch 1882 - loss: 0.5016
lr 0.00000080 - epoch 1883 - loss: 0.5061
lr 0.00000080 - epoch 1884 - loss: 0.5080
lr 0.00000080 - epoch 1885 - loss: 0.5069
lr 0.00000080 - epoch 1886 - loss: 0.5004
lr 0.00000080 - epoch 1887 - loss: 0.5120
lr 0.00000080 - epoch 1888 - loss: 0.5149
lr 0.00000080 - epoch 1889 - loss: 0.5081
lr 0.00000080 - epoch 1890 - loss: 0.5058
lr 0.00000080 - epoch 1891 - loss: 0.5065
lr 0.00000080 - epoch 1892 - loss: 0.5110
lr 0.00000080 - epoch 1893 - loss: 0.5063
lr 0.00000080 - epoch 1894 - loss: 0.5116
lr 0.00000080 - epoch 1895 - loss: 0.5137
lr 0.00000080 - epoch 1896 - loss: 0.5040
lr 0.00000080 - epoch 1897 - loss: 0.4997
lr 0.00000080 - epoch 1898 - loss: 0.5049
lr 0.00000080 - epoch 1899 - loss: 0.5003
lr 0.00000080 - epoch 1900 - loss: 0.5062
lr 0.00000080 - epoch 1901 - loss: 0.5050
lr 0.00000080 - epoch 1902 - loss: 0.5050
lr 0.00000080 - epoch 1903 - loss:

lr 0.00000080 - epoch 2077 - loss: 0.5091
lr 0.00000080 - epoch 2078 - loss: 0.4933
lr 0.00000080 - epoch 2079 - loss: 0.4977
lr 0.00000080 - epoch 2080 - loss: 0.4893
lr 0.00000080 - epoch 2081 - loss: 0.4930
lr 0.00000080 - epoch 2082 - loss: 0.4939
lr 0.00000080 - epoch 2083 - loss: 0.4899
lr 0.00000080 - epoch 2084 - loss: 0.4912
lr 0.00000080 - epoch 2085 - loss: 0.5029
lr 0.00000080 - epoch 2086 - loss: 0.4921
lr 0.00000080 - epoch 2087 - loss: 0.4814
lr 0.00000080 - epoch 2088 - loss: 0.4904
lr 0.00000080 - epoch 2089 - loss: 0.4914
lr 0.00000080 - epoch 2090 - loss: 0.4880
lr 0.00000080 - epoch 2091 - loss: 0.4910
lr 0.00000080 - epoch 2092 - loss: 0.4871
lr 0.00000080 - epoch 2093 - loss: 0.4854
lr 0.00000080 - epoch 2094 - loss: 0.4896
lr 0.00000080 - epoch 2095 - loss: 0.4877
lr 0.00000080 - epoch 2096 - loss: 0.4806
lr 0.00000080 - epoch 2097 - loss: 0.4836
lr 0.00000080 - epoch 2098 - loss: 0.4871
lr 0.00000080 - epoch 2099 - loss: 0.4864
lr 0.00000080 - epoch 2100 - loss:

lr 0.00000080 - epoch 2276 - loss: 0.4688
lr 0.00000080 - epoch 2277 - loss: 0.4701
lr 0.00000080 - epoch 2278 - loss: 0.4787
lr 0.00000080 - epoch 2279 - loss: 0.4716
lr 0.00000080 - epoch 2280 - loss: 0.4711
lr 0.00000080 - epoch 2281 - loss: 0.4745
lr 0.00000080 - epoch 2282 - loss: 0.4707
lr 0.00000080 - epoch 2283 - loss: 0.4722
lr 0.00000080 - epoch 2284 - loss: 0.4746
lr 0.00000080 - epoch 2285 - loss: 0.4789
lr 0.00000080 - epoch 2286 - loss: 0.4635
lr 0.00000080 - epoch 2287 - loss: 0.4748
lr 0.00000080 - epoch 2288 - loss: 0.4655
lr 0.00000080 - epoch 2289 - loss: 0.4699
lr 0.00000080 - epoch 2290 - loss: 0.4684
lr 0.00000080 - epoch 2291 - loss: 0.4666
lr 0.00000080 - epoch 2292 - loss: 0.4645
lr 0.00000080 - epoch 2293 - loss: 0.4697
lr 0.00000080 - epoch 2294 - loss: 0.4667
lr 0.00000080 - epoch 2295 - loss: 0.4723
lr 0.00000080 - epoch 2296 - loss: 0.4717
lr 0.00000080 - epoch 2297 - loss: 0.4754
lr 0.00000080 - epoch 2298 - loss: 0.4809
lr 0.00000080 - epoch 2299 - loss:

lr 0.00000080 - epoch 2475 - loss: 0.4491
lr 0.00000080 - epoch 2476 - loss: 0.4526
lr 0.00000080 - epoch 2477 - loss: 0.4496
lr 0.00000080 - epoch 2478 - loss: 0.4433
lr 0.00000080 - epoch 2479 - loss: 0.4416
lr 0.00000080 - epoch 2480 - loss: 0.4382
lr 0.00000080 - epoch 2481 - loss: 0.4372
lr 0.00000080 - epoch 2482 - loss: 0.4396
lr 0.00000080 - epoch 2483 - loss: 0.4418
lr 0.00000080 - epoch 2484 - loss: 0.4372
lr 0.00000080 - epoch 2485 - loss: 0.4441
lr 0.00000080 - epoch 2486 - loss: 0.4432
lr 0.00000080 - epoch 2487 - loss: 0.4418
lr 0.00000080 - epoch 2488 - loss: 0.4429
lr 0.00000080 - epoch 2489 - loss: 0.4441
lr 0.00000080 - epoch 2490 - loss: 0.4489
lr 0.00000080 - epoch 2491 - loss: 0.4546
lr 0.00000080 - epoch 2492 - loss: 0.4511
lr 0.00000080 - epoch 2493 - loss: 0.4447
lr 0.00000080 - epoch 2494 - loss: 0.4391
lr 0.00000080 - epoch 2495 - loss: 0.4466
lr 0.00000080 - epoch 2496 - loss: 0.4458
lr 0.00000080 - epoch 2497 - loss: 0.4464
lr 0.00000080 - epoch 2498 - loss:

In [6]:
np.mean(val_results,0)
# 6e-6 with lowest RMSE
# 8e-7
# 9e-7
# 9e-7

array([2.70944822, 2.7068392 , 2.87735069, 2.88182998, 2.73524535,
       2.81038594, 2.75270534, 2.67501211, 3.05368602])

## pSGLD

In [7]:
import torch
import torchvision
import os

from itertools import chain
from torch import nn
from torchvision import transforms
import torch.nn.functional as F
import numpy as np

import psgld 

np.random.seed(42)
torch.manual_seed(42)




if torch.cuda.is_available():
    device = torch.device("cuda")
else:
    device = torch.device("cpu")



lambda_ = 1.
# learning_rates = [1e-1, 1e-2, 1e-3, 1e-4, 1e-5, 1e-6, 1e-7, 1e-8, 1e-9, 1e-10, 1e-11]
# learning_rates = [5e-2, 3e-2, 1e-2, 9e-3, 7e-3, 5e-3, 3e-3, 1e-3, 9e-4, 8e-4, 6e-4]
learning_rates = [1e-2, 9e-3, 8e-3, 7e-3, 6e-3, 5e-3, 4e-3, 2e-3, 1e-3]
alpha = 0.99


batch_size = 32
dataset_size= 416

n_chains = 10
n_samples = 300


val_results = np.zeros((5,9))


for i in range(5):
    for j,lr in enumerate(learning_rates):
        network = Model()
        criterion = nn.MSELoss(size_average=False)
        optim = psgld.optim.psgld(network, lr, alpha, lambda_, batch_size, dataset_size)
        evaluate = evaluation(test_loader, n_samples, X_train_mean, X_train_std, y_train_mean, y_train_std)

        t = 1
        n = 0
        for epoch in range(2500):

            running_loss = 0
            for x, y in iter(train_loader):
                x = x.view(x.size(0), -1)

                network.zero_grad()
                output = network(x)
                loss = 0.5 * criterion(output, y)
                loss.backward()
                optim.step()
g_i

                running_loss += loss * batch_size / dataset_size


                if (t >= 300) & (t % 100 == 0) & (n < n_samples):
                    rmse = evaluate.rmse(network)
                    n += 1
                t += 1.
            print("lr {:.8f} - epoch {:d} - loss: {:.4f}".format(lr, epoch, running_loss))
        val_results[i,j] = rmse

/opt/anaconda/envs/Python3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))


lr 0.01000000 - epoch 0 - loss: 74.2480
lr 0.01000000 - epoch 1 - loss: 5.4785
lr 0.01000000 - epoch 2 - loss: 4.5483
lr 0.01000000 - epoch 3 - loss: 4.0681
lr 0.01000000 - epoch 4 - loss: 3.8320
lr 0.01000000 - epoch 5 - loss: 3.5489
lr 0.01000000 - epoch 6 - loss: 3.3672
lr 0.01000000 - epoch 7 - loss: 3.2122
lr 0.01000000 - epoch 8 - loss: 3.0405
lr 0.01000000 - epoch 9 - loss: 2.9872
lr 0.01000000 - epoch 10 - loss: 2.8969
lr 0.01000000 - epoch 11 - loss: 2.8889
lr 0.01000000 - epoch 12 - loss: 2.7663
lr 0.01000000 - epoch 13 - loss: 2.9267
lr 0.01000000 - epoch 14 - loss: 2.8622
lr 0.01000000 - epoch 15 - loss: 2.7672
lr 0.01000000 - epoch 16 - loss: 2.7961
lr 0.01000000 - epoch 17 - loss: 2.8075
lr 0.01000000 - epoch 18 - loss: 2.5757
lr 0.01000000 - epoch 19 - loss: 2.5523
lr 0.01000000 - epoch 20 - loss: 2.4287
lr 0.01000000 - epoch 21 - loss: 2.5755
lr 0.01000000 - epoch 22 - loss: 2.5739
lr 0.01000000 - epoch 23 - loss: 2.9431


/opt/anaconda/envs/Python3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='elementwise_mean' instead.
  warnings.warn(warning.format(ret))


lr 0.01000000 - epoch 24 - loss: 2.4746
lr 0.01000000 - epoch 25 - loss: 2.1690
lr 0.01000000 - epoch 26 - loss: 2.6796
lr 0.01000000 - epoch 27 - loss: 2.4475
lr 0.01000000 - epoch 28 - loss: 2.0714
lr 0.01000000 - epoch 29 - loss: 2.5119
lr 0.01000000 - epoch 30 - loss: 2.2867
lr 0.01000000 - epoch 31 - loss: 2.3627
lr 0.01000000 - epoch 32 - loss: 2.3884
lr 0.01000000 - epoch 33 - loss: 2.3497
lr 0.01000000 - epoch 34 - loss: 2.9702
lr 0.01000000 - epoch 35 - loss: 1.8793
lr 0.01000000 - epoch 36 - loss: 2.2275
lr 0.01000000 - epoch 37 - loss: 2.1150
lr 0.01000000 - epoch 38 - loss: 1.9491
lr 0.01000000 - epoch 39 - loss: 2.5364
lr 0.01000000 - epoch 40 - loss: 2.0723
lr 0.01000000 - epoch 41 - loss: 1.9179
lr 0.01000000 - epoch 42 - loss: 2.5702
lr 0.01000000 - epoch 43 - loss: 1.8298
lr 0.01000000 - epoch 44 - loss: 2.2180
lr 0.01000000 - epoch 45 - loss: 1.6493
lr 0.01000000 - epoch 46 - loss: 2.0861
lr 0.01000000 - epoch 47 - loss: 2.1264
lr 0.01000000 - epoch 48 - loss: 2.4647


lr 0.01000000 - epoch 226 - loss: 1.1291
lr 0.01000000 - epoch 227 - loss: 1.2111
lr 0.01000000 - epoch 228 - loss: 1.6046
lr 0.01000000 - epoch 229 - loss: 1.3843
lr 0.01000000 - epoch 230 - loss: 1.9359
lr 0.01000000 - epoch 231 - loss: 1.6535
lr 0.01000000 - epoch 232 - loss: 2.0935
lr 0.01000000 - epoch 233 - loss: 1.8624
lr 0.01000000 - epoch 234 - loss: 1.4174
lr 0.01000000 - epoch 235 - loss: 1.0979
lr 0.01000000 - epoch 236 - loss: 1.3698
lr 0.01000000 - epoch 237 - loss: 2.5806
lr 0.01000000 - epoch 238 - loss: 2.8785
lr 0.01000000 - epoch 239 - loss: 2.3539
lr 0.01000000 - epoch 240 - loss: 1.3223
lr 0.01000000 - epoch 241 - loss: 1.3102
lr 0.01000000 - epoch 242 - loss: 1.6406
lr 0.01000000 - epoch 243 - loss: 2.4976
lr 0.01000000 - epoch 244 - loss: 1.5533
lr 0.01000000 - epoch 245 - loss: 1.9485
lr 0.01000000 - epoch 246 - loss: 1.9764
lr 0.01000000 - epoch 247 - loss: 1.6766
lr 0.01000000 - epoch 248 - loss: 1.5338
lr 0.01000000 - epoch 249 - loss: 1.7251
lr 0.01000000 - 

...

lr 0.00100000 - epoch 1663 - loss: 0.6243
lr 0.00100000 - epoch 1664 - loss: 0.6319
lr 0.00100000 - epoch 1665 - loss: 0.6125
lr 0.00100000 - epoch 1666 - loss: 0.6611
lr 0.00100000 - epoch 1667 - loss: 0.5944
lr 0.00100000 - epoch 1668 - loss: 0.6504
lr 0.00100000 - epoch 1669 - loss: 0.5985
lr 0.00100000 - epoch 1670 - loss: 0.6888
lr 0.00100000 - epoch 1671 - loss: 0.6703
lr 0.00100000 - epoch 1672 - loss: 0.7318
lr 0.00100000 - epoch 1673 - loss: 0.6598
lr 0.00100000 - epoch 1674 - loss: 0.6658
lr 0.00100000 - epoch 1675 - loss: 0.6619
lr 0.00100000 - epoch 1676 - loss: 0.6620
lr 0.00100000 - epoch 1677 - loss: 0.6785
lr 0.00100000 - epoch 1678 - loss: 0.6736
lr 0.00100000 - epoch 1679 - loss: 0.6509
lr 0.00100000 - epoch 1680 - loss: 0.6791
lr 0.00100000 - epoch 1681 - loss: 0.6974
lr 0.00100000 - epoch 1682 - loss: 0.7080
lr 0.00100000 - epoch 1683 - loss: 0.6493
lr 0.00100000 - epoch 1684 - loss: 0.6457
lr 0.00100000 - epoch 1685 - loss: 0.6491
lr 0.00100000 - epoch 1686 - loss:

lr 0.00100000 - epoch 1861 - loss: 0.6783
lr 0.00100000 - epoch 1862 - loss: 0.6570
lr 0.00100000 - epoch 1863 - loss: 0.6181
lr 0.00100000 - epoch 1864 - loss: 0.7328
lr 0.00100000 - epoch 1865 - loss: 0.6876
lr 0.00100000 - epoch 1866 - loss: 0.6678
lr 0.00100000 - epoch 1867 - loss: 0.6938
lr 0.00100000 - epoch 1868 - loss: 0.6164
lr 0.00100000 - epoch 1869 - loss: 0.6000
lr 0.00100000 - epoch 1870 - loss: 0.6505
lr 0.00100000 - epoch 1871 - loss: 0.7137
lr 0.00100000 - epoch 1872 - loss: 0.8210
lr 0.00100000 - epoch 1873 - loss: 0.6702
lr 0.00100000 - epoch 1874 - loss: 0.7382
lr 0.00100000 - epoch 1875 - loss: 0.7216
lr 0.00100000 - epoch 1876 - loss: 0.7211
lr 0.00100000 - epoch 1877 - loss: 0.5972
lr 0.00100000 - epoch 1878 - loss: 0.6127
lr 0.00100000 - epoch 1879 - loss: 0.6662
lr 0.00100000 - epoch 1880 - loss: 0.6612
lr 0.00100000 - epoch 1881 - loss: 0.6467
lr 0.00100000 - epoch 1882 - loss: 0.7057
lr 0.00100000 - epoch 1883 - loss: 0.6569
lr 0.00100000 - epoch 1884 - loss:

lr 0.00100000 - epoch 2060 - loss: 0.7235
lr 0.00100000 - epoch 2061 - loss: 0.6466
lr 0.00100000 - epoch 2062 - loss: 0.6493
lr 0.00100000 - epoch 2063 - loss: 0.6400
lr 0.00100000 - epoch 2064 - loss: 0.6035
lr 0.00100000 - epoch 2065 - loss: 0.6213
lr 0.00100000 - epoch 2066 - loss: 0.7418
lr 0.00100000 - epoch 2067 - loss: 0.6416
lr 0.00100000 - epoch 2068 - loss: 0.6680
lr 0.00100000 - epoch 2069 - loss: 0.7146
lr 0.00100000 - epoch 2070 - loss: 0.7051
lr 0.00100000 - epoch 2071 - loss: 0.7228
lr 0.00100000 - epoch 2072 - loss: 0.6745
lr 0.00100000 - epoch 2073 - loss: 0.6370
lr 0.00100000 - epoch 2074 - loss: 0.6979
lr 0.00100000 - epoch 2075 - loss: 0.6571
lr 0.00100000 - epoch 2076 - loss: 0.7640
lr 0.00100000 - epoch 2077 - loss: 0.6107
lr 0.00100000 - epoch 2078 - loss: 0.6061
lr 0.00100000 - epoch 2079 - loss: 0.6889
lr 0.00100000 - epoch 2080 - loss: 0.6106
lr 0.00100000 - epoch 2081 - loss: 0.6546
lr 0.00100000 - epoch 2082 - loss: 0.6454
lr 0.00100000 - epoch 2083 - loss:

lr 0.00100000 - epoch 2256 - loss: 0.6928
lr 0.00100000 - epoch 2257 - loss: 0.6809
lr 0.00100000 - epoch 2258 - loss: 0.6164
lr 0.00100000 - epoch 2259 - loss: 0.6783
lr 0.00100000 - epoch 2260 - loss: 0.6008
lr 0.00100000 - epoch 2261 - loss: 0.6109
lr 0.00100000 - epoch 2262 - loss: 0.7454
lr 0.00100000 - epoch 2263 - loss: 0.6221
lr 0.00100000 - epoch 2264 - loss: 0.7028
lr 0.00100000 - epoch 2265 - loss: 0.6272
lr 0.00100000 - epoch 2266 - loss: 0.7387
lr 0.00100000 - epoch 2267 - loss: 0.6326
lr 0.00100000 - epoch 2268 - loss: 0.7022
lr 0.00100000 - epoch 2269 - loss: 0.7233
lr 0.00100000 - epoch 2270 - loss: 0.8191
lr 0.00100000 - epoch 2271 - loss: 0.6907
lr 0.00100000 - epoch 2272 - loss: 0.6558
lr 0.00100000 - epoch 2273 - loss: 0.6376
lr 0.00100000 - epoch 2274 - loss: 0.6281
lr 0.00100000 - epoch 2275 - loss: 0.7107
lr 0.00100000 - epoch 2276 - loss: 0.6562
lr 0.00100000 - epoch 2277 - loss: 0.6645
lr 0.00100000 - epoch 2278 - loss: 0.6651
lr 0.00100000 - epoch 2279 - loss:

lr 0.00100000 - epoch 2456 - loss: 0.5798
lr 0.00100000 - epoch 2457 - loss: 0.6222
lr 0.00100000 - epoch 2458 - loss: 0.5990
lr 0.00100000 - epoch 2459 - loss: 0.6390
lr 0.00100000 - epoch 2460 - loss: 0.5980
lr 0.00100000 - epoch 2461 - loss: 0.5963
lr 0.00100000 - epoch 2462 - loss: 0.6662
lr 0.00100000 - epoch 2463 - loss: 0.6532
lr 0.00100000 - epoch 2464 - loss: 0.6852
lr 0.00100000 - epoch 2465 - loss: 0.6952
lr 0.00100000 - epoch 2466 - loss: 0.6171
lr 0.00100000 - epoch 2467 - loss: 0.6718
lr 0.00100000 - epoch 2468 - loss: 0.8232
lr 0.00100000 - epoch 2469 - loss: 0.6627
lr 0.00100000 - epoch 2470 - loss: 0.6894
lr 0.00100000 - epoch 2471 - loss: 0.7327
lr 0.00100000 - epoch 2472 - loss: 0.6213
lr 0.00100000 - epoch 2473 - loss: 0.7168
lr 0.00100000 - epoch 2474 - loss: 0.6403
lr 0.00100000 - epoch 2475 - loss: 0.5972
lr 0.00100000 - epoch 2476 - loss: 0.5979
lr 0.00100000 - epoch 2477 - loss: 0.6456
lr 0.00100000 - epoch 2478 - loss: 0.5736
lr 0.00100000 - epoch 2479 - loss:

In [8]:
np.mean(val_results,0)
# 7e-3
# 1e-3
# 7e-3
# 5e-3

array([2.52235413, 2.64663625, 2.55350018, 2.52644193, 2.8088516 ,
       2.44745815, 2.62417281, 2.69466531, 2.56149352])

## K-SGLD

In [9]:
import torch
#import torchvision
import os

from itertools import chain
from torch import nn
#from torchvision import transforms
import torch.nn.functional as F
import numpy as np
#from numpy.random import RandomState

import ksgld


np.random.seed(42)
torch.manual_seed(42)


if torch.cuda.is_available():
    device = torch.device("cuda")
else:
    device = torch.device("cpu")


batch_size = 32
dataset_size=416

n_chains = 10
n_samples = 300

val_results = np.zeros((5,10))

learning_rates = [7e-4, 6e-4, 5e-4, 4e-4, 3e-4, 2e-4, 1e-4, 9e-5, 8e-5]


val_results = np.zeros((5,9))


losses_ksgld = []
for i in range(5):
    for j,lr in enumerate(learning_rates):
        network = Model()
        criterion = nn.MSELoss(size_average=False)
        optim = ksgld.optim.KSGLD(network, criterion, batch_size, dataset_size, eta=1., v=0., lambda_=1., epsilon=lr, l2=1e-3, invert_every=1)
        evaluate = evaluation(test_loader, n_samples, X_train_mean, X_train_std, y_train_mean, y_train_std)

        t = 1.
        n = 0


        for epoch in range(2500):
            running_loss = 0
            for x, y in iter(train_loader):
                x = x.view(x.size(0), -1)

                optim.update_curvature(x)

                network.zero_grad()
                output = network(x)
                loss = 0.5 * criterion(output, y)
                loss.backward()
                optim.step()

                running_loss += loss * batch_size / dataset_size

                if (t >= 300) & (t % 100 == 0) & (n < n_samples):
                    rmse = evaluate.rmse(network)
                    n += 1
                t += 1.
            print("lr {:.8f} - epoch {:d} - loss: {:.4f}".format(lr, epoch, running_loss))
        val_results[i,j] = rmse

/opt/anaconda/envs/Python3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))
/opt/anaconda/envs/Python3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='none' instead.
  warnings.warn(warning.format(ret))


lr 0.00070000 - epoch 0 - loss: 8.4925
lr 0.00070000 - epoch 1 - loss: 5.3030
lr 0.00070000 - epoch 2 - loss: 5.0478
lr 0.00070000 - epoch 3 - loss: 4.4528
lr 0.00070000 - epoch 4 - loss: 4.6313
lr 0.00070000 - epoch 5 - loss: 4.9988
lr 0.00070000 - epoch 6 - loss: 5.8043
lr 0.00070000 - epoch 7 - loss: 5.9427
lr 0.00070000 - epoch 8 - loss: 7.7108
lr 0.00070000 - epoch 9 - loss: 7.2815
lr 0.00070000 - epoch 10 - loss: 6.5574
lr 0.00070000 - epoch 11 - loss: 8.8911
lr 0.00070000 - epoch 12 - loss: 10.8969
lr 0.00070000 - epoch 13 - loss: 8.5583
lr 0.00070000 - epoch 14 - loss: 7.9456
lr 0.00070000 - epoch 15 - loss: 9.3843
lr 0.00070000 - epoch 16 - loss: 10.0667
lr 0.00070000 - epoch 17 - loss: 10.0107
lr 0.00070000 - epoch 18 - loss: 9.2241
lr 0.00070000 - epoch 19 - loss: 10.1184
lr 0.00070000 - epoch 20 - loss: 11.5692
lr 0.00070000 - epoch 21 - loss: 15.3758
lr 0.00070000 - epoch 22 - loss: 11.6231


/opt/anaconda/envs/Python3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='elementwise_mean' instead.
  warnings.warn(warning.format(ret))


lr 0.00070000 - epoch 23 - loss: 12.0722
lr 0.00070000 - epoch 24 - loss: 14.8811
lr 0.00070000 - epoch 25 - loss: 14.4021
lr 0.00070000 - epoch 26 - loss: 13.4740
lr 0.00070000 - epoch 27 - loss: 15.4938
lr 0.00070000 - epoch 28 - loss: 12.4603
lr 0.00070000 - epoch 29 - loss: 12.4795
lr 0.00070000 - epoch 30 - loss: 11.4503
lr 0.00070000 - epoch 31 - loss: 14.2133
lr 0.00070000 - epoch 32 - loss: 10.3875
lr 0.00070000 - epoch 33 - loss: 10.7484
lr 0.00070000 - epoch 34 - loss: 17.2688
lr 0.00070000 - epoch 35 - loss: 12.9235
lr 0.00070000 - epoch 36 - loss: 13.6266
lr 0.00070000 - epoch 37 - loss: 10.3281
lr 0.00070000 - epoch 38 - loss: 9.5114
lr 0.00070000 - epoch 39 - loss: 10.3443
lr 0.00070000 - epoch 40 - loss: 12.4641
lr 0.00070000 - epoch 41 - loss: 13.1533
lr 0.00070000 - epoch 42 - loss: 12.6861
lr 0.00070000 - epoch 43 - loss: 13.8682
lr 0.00070000 - epoch 44 - loss: 12.6664
lr 0.00070000 - epoch 45 - loss: 13.6495
lr 0.00070000 - epoch 46 - loss: 15.4164
lr 0.00070000 - e

lr 0.00070000 - epoch 222 - loss: 8.7103
lr 0.00070000 - epoch 223 - loss: 9.9624
lr 0.00070000 - epoch 224 - loss: 12.0844
lr 0.00070000 - epoch 225 - loss: 10.8371
lr 0.00070000 - epoch 226 - loss: 12.2930
lr 0.00070000 - epoch 227 - loss: 10.4600
lr 0.00070000 - epoch 228 - loss: 9.3909
lr 0.00070000 - epoch 229 - loss: 13.2003
lr 0.00070000 - epoch 230 - loss: 8.6544
lr 0.00070000 - epoch 231 - loss: 10.1205
lr 0.00070000 - epoch 232 - loss: 10.3388
lr 0.00070000 - epoch 233 - loss: 11.1979
lr 0.00070000 - epoch 234 - loss: 9.2893
lr 0.00070000 - epoch 235 - loss: 11.7413
lr 0.00070000 - epoch 236 - loss: 14.6911
lr 0.00070000 - epoch 237 - loss: 16.5997
lr 0.00070000 - epoch 238 - loss: 11.8308
lr 0.00070000 - epoch 239 - loss: 7.9085
lr 0.00070000 - epoch 240 - loss: 8.4790
lr 0.00070000 - epoch 241 - loss: 8.0981
lr 0.00070000 - epoch 242 - loss: 7.3262
lr 0.00070000 - epoch 243 - loss: 9.7350
lr 0.00070000 - epoch 244 - loss: 9.9486
lr 0.00070000 - epoch 245 - loss: 10.8981
lr 

...

lr 0.00030000 - epoch 2012 - loss: 7.2653
lr 0.00030000 - epoch 2013 - loss: 8.0892
lr 0.00030000 - epoch 2014 - loss: 6.9226
lr 0.00030000 - epoch 2015 - loss: 6.7489
lr 0.00030000 - epoch 2016 - loss: 8.3273
lr 0.00030000 - epoch 2017 - loss: 9.3998
lr 0.00030000 - epoch 2018 - loss: 9.1586
lr 0.00030000 - epoch 2019 - loss: 8.4240
lr 0.00030000 - epoch 2020 - loss: 9.2934
lr 0.00030000 - epoch 2021 - loss: 9.3194
lr 0.00030000 - epoch 2022 - loss: 9.3207
lr 0.00030000 - epoch 2023 - loss: 10.1519
lr 0.00030000 - epoch 2024 - loss: 9.6885
lr 0.00030000 - epoch 2025 - loss: 9.7069
lr 0.00030000 - epoch 2026 - loss: 10.7961
lr 0.00030000 - epoch 2027 - loss: 10.0568
lr 0.00030000 - epoch 2028 - loss: 10.1801
lr 0.00030000 - epoch 2029 - loss: 11.2362
lr 0.00030000 - epoch 2030 - loss: 10.4441
lr 0.00030000 - epoch 2031 - loss: 9.2801
lr 0.00030000 - epoch 2032 - loss: 9.8176
lr 0.00030000 - epoch 2033 - loss: 12.2390
lr 0.00030000 - epoch 2034 - loss: 11.4142
lr 0.00030000 - epoch 2035

lr 0.00030000 - epoch 2207 - loss: 7.4888
lr 0.00030000 - epoch 2208 - loss: 8.6370
lr 0.00030000 - epoch 2209 - loss: 8.4593
lr 0.00030000 - epoch 2210 - loss: 9.6044
lr 0.00030000 - epoch 2211 - loss: 10.3755
lr 0.00030000 - epoch 2212 - loss: 9.7591
lr 0.00030000 - epoch 2213 - loss: 9.1724
lr 0.00030000 - epoch 2214 - loss: 7.9629
lr 0.00030000 - epoch 2215 - loss: 8.4632
lr 0.00030000 - epoch 2216 - loss: 7.5980
lr 0.00030000 - epoch 2217 - loss: 6.9609
lr 0.00030000 - epoch 2218 - loss: 6.6588
lr 0.00030000 - epoch 2219 - loss: 7.9196
lr 0.00030000 - epoch 2220 - loss: 8.1683
lr 0.00030000 - epoch 2221 - loss: 7.8278
lr 0.00030000 - epoch 2222 - loss: 6.9843
lr 0.00030000 - epoch 2223 - loss: 6.3597
lr 0.00030000 - epoch 2224 - loss: 7.3808
lr 0.00030000 - epoch 2225 - loss: 6.4658
lr 0.00030000 - epoch 2226 - loss: 5.7033
lr 0.00030000 - epoch 2227 - loss: 6.7143
lr 0.00030000 - epoch 2228 - loss: 6.1749
lr 0.00030000 - epoch 2229 - loss: 5.8353
lr 0.00030000 - epoch 2230 - loss

lr 0.00030000 - epoch 2401 - loss: 8.9119
lr 0.00030000 - epoch 2402 - loss: 8.4860
lr 0.00030000 - epoch 2403 - loss: 7.8541
lr 0.00030000 - epoch 2404 - loss: 7.8745
lr 0.00030000 - epoch 2405 - loss: 7.9758
lr 0.00030000 - epoch 2406 - loss: 7.7917
lr 0.00030000 - epoch 2407 - loss: 7.8053
lr 0.00030000 - epoch 2408 - loss: 7.9006
lr 0.00030000 - epoch 2409 - loss: 7.7129
lr 0.00030000 - epoch 2410 - loss: 6.7704
lr 0.00030000 - epoch 2411 - loss: 7.4871
lr 0.00030000 - epoch 2412 - loss: 7.2725
lr 0.00030000 - epoch 2413 - loss: 11.5429
lr 0.00030000 - epoch 2414 - loss: 10.9484
lr 0.00030000 - epoch 2415 - loss: 8.1475
lr 0.00030000 - epoch 2416 - loss: 7.5021
lr 0.00030000 - epoch 2417 - loss: 7.1162
lr 0.00030000 - epoch 2418 - loss: 7.5376
lr 0.00030000 - epoch 2419 - loss: 7.2782
lr 0.00030000 - epoch 2420 - loss: 7.0495
lr 0.00030000 - epoch 2421 - loss: 7.1486
lr 0.00030000 - epoch 2422 - loss: 8.7073
lr 0.00030000 - epoch 2423 - loss: 7.8997
lr 0.00030000 - epoch 2424 - los

lr 0.00020000 - epoch 102 - loss: 10.5269
lr 0.00020000 - epoch 103 - loss: 11.4117
lr 0.00020000 - epoch 104 - loss: 10.3508
lr 0.00020000 - epoch 105 - loss: 11.4513
lr 0.00020000 - epoch 106 - loss: 9.2719
lr 0.00020000 - epoch 107 - loss: 8.9967
lr 0.00020000 - epoch 108 - loss: 10.1184
lr 0.00020000 - epoch 109 - loss: 13.8694
lr 0.00020000 - epoch 110 - loss: 16.1395
lr 0.00020000 - epoch 111 - loss: 12.3455
lr 0.00020000 - epoch 112 - loss: 14.2782
lr 0.00020000 - epoch 113 - loss: 13.1269
lr 0.00020000 - epoch 114 - loss: 11.8995
lr 0.00020000 - epoch 115 - loss: 12.2619
lr 0.00020000 - epoch 116 - loss: 12.7449
lr 0.00020000 - epoch 117 - loss: 13.1942
lr 0.00020000 - epoch 118 - loss: 12.5082
lr 0.00020000 - epoch 119 - loss: 12.2829
lr 0.00020000 - epoch 120 - loss: 11.6944
lr 0.00020000 - epoch 121 - loss: 11.5866
lr 0.00020000 - epoch 122 - loss: 12.2430
lr 0.00020000 - epoch 123 - loss: 10.9519
lr 0.00020000 - epoch 124 - loss: 11.9633
lr 0.00020000 - epoch 125 - loss: 12

KeyboardInterrupt: 

In [6]:
np.mean(val_results[:2,:],0)
#5e-4
#6e-4

array([2.84194732, 2.74504006, 2.86489904, 2.7881825 , 2.79351056,
       3.04386258, 3.70367503, 3.76106298, 3.19219208])

## K-SGFS

In [11]:
import torch
#import torchvision
import os

from itertools import chain
from torch import nn
#from torchvision import transforms
import torch.nn.functional as F
import numpy as np
#from numpy.random import RandomState

import ksgfs


np.random.seed(42)
torch.manual_seed(42)


if torch.cuda.is_available():
    device = torch.device("cuda")
else:
    device = torch.device("cpu")


batch_size = 32
dataset_size= 416

n_chains = 10
n_samples = 300


#learning_rates = [1e-1, 1e-2, 1e-3, 1e-4, 1e-5]
learning_rates = [2e-1, 1e-1, 9e-2, 8e-2, 7e-2, 6e-2, 5e-2, 4e-2, 3e-2, 2e-2, 1e-2]


val_results = np.zeros((5,11))


losses_ksgld = []
for i in range(5):
    for j,lr in enumerate(learning_rates):
        network = Model()
        criterion = nn.MSELoss(size_average=False)
        optim = ksgfs.optim.KSGFS(network, criterion, batch_size, dataset_size, eta=1., v=0., lambda_=1., epsilon=lr, l2=1e-3, invert_every=1)
        evaluate = evaluation(test_loader, n_samples, X_train_mean, X_train_std, y_train_mean, y_train_std)

        t = 1.
        n = 0


        for epoch in range(2500):
            running_loss = 0
            for x, y in iter(train_loader):
                x = x.view(x.size(0), -1)

                optim.update_curvature(x)

                network.zero_grad()
                output = network(x)
                loss = 0.5 * criterion(output, y)
                loss.backward()
                optim.step()

                running_loss += loss * batch_size / dataset_size

                if (t >= 300) & (t % 100 == 0) & (n < n_samples):
                    rmse = evaluate.rmse(network)
                    n += 1
                t += 1.
            print("lr {:.8f} - epoch {:d} - loss: {:.4f}".format(lr, epoch, running_loss))
        val_results[i,j] = rmse

/opt/anaconda/envs/Python3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))
/opt/anaconda/envs/Python3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='none' instead.
  warnings.warn(warning.format(ret))


lr 0.20000000 - epoch 0 - loss: 20.3792
lr 0.20000000 - epoch 1 - loss: 7.5945
lr 0.20000000 - epoch 2 - loss: 5.3204
lr 0.20000000 - epoch 3 - loss: 5.0204
lr 0.20000000 - epoch 4 - loss: 4.9954
lr 0.20000000 - epoch 5 - loss: 10.7136
lr 0.20000000 - epoch 6 - loss: 7.3603
lr 0.20000000 - epoch 7 - loss: 8.0571
lr 0.20000000 - epoch 8 - loss: 4.4543
lr 0.20000000 - epoch 9 - loss: 6.1320
lr 0.20000000 - epoch 10 - loss: 4.1001
lr 0.20000000 - epoch 11 - loss: 5.6612
lr 0.20000000 - epoch 12 - loss: 4.4453
lr 0.20000000 - epoch 13 - loss: 7.0213
lr 0.20000000 - epoch 14 - loss: 5.6990
lr 0.20000000 - epoch 15 - loss: 4.2381
lr 0.20000000 - epoch 16 - loss: 6.0299
lr 0.20000000 - epoch 17 - loss: 4.2581
lr 0.20000000 - epoch 18 - loss: 5.5266
lr 0.20000000 - epoch 19 - loss: 5.8572
lr 0.20000000 - epoch 20 - loss: 5.5490
lr 0.20000000 - epoch 21 - loss: 3.5580
lr 0.20000000 - epoch 22 - loss: 2.9246


/opt/anaconda/envs/Python3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='elementwise_mean' instead.
  warnings.warn(warning.format(ret))


lr 0.20000000 - epoch 23 - loss: 4.1576
lr 0.20000000 - epoch 24 - loss: 5.9430
lr 0.20000000 - epoch 25 - loss: 4.9373
lr 0.20000000 - epoch 26 - loss: 4.2229
lr 0.20000000 - epoch 27 - loss: 3.9444
lr 0.20000000 - epoch 28 - loss: 3.2979
lr 0.20000000 - epoch 29 - loss: 4.0478
lr 0.20000000 - epoch 30 - loss: 4.0526
lr 0.20000000 - epoch 31 - loss: 5.1485
lr 0.20000000 - epoch 32 - loss: 3.5834
lr 0.20000000 - epoch 33 - loss: 3.9396
lr 0.20000000 - epoch 34 - loss: 5.7716
lr 0.20000000 - epoch 35 - loss: 3.8397
lr 0.20000000 - epoch 36 - loss: 5.8012
lr 0.20000000 - epoch 37 - loss: 7.5407
lr 0.20000000 - epoch 38 - loss: 6.5091
lr 0.20000000 - epoch 39 - loss: 5.3330
lr 0.20000000 - epoch 40 - loss: 7.9903
lr 0.20000000 - epoch 41 - loss: 6.4897
lr 0.20000000 - epoch 42 - loss: 4.8097
lr 0.20000000 - epoch 43 - loss: 3.7446
lr 0.20000000 - epoch 44 - loss: 5.7078
lr 0.20000000 - epoch 45 - loss: 3.9767
lr 0.20000000 - epoch 46 - loss: 7.2023
lr 0.20000000 - epoch 47 - loss: 6.1440


lr 0.20000000 - epoch 225 - loss: 2.6723
lr 0.20000000 - epoch 226 - loss: 8.0394
lr 0.20000000 - epoch 227 - loss: 2.5442
lr 0.20000000 - epoch 228 - loss: 2.2649
lr 0.20000000 - epoch 229 - loss: 2.7957
lr 0.20000000 - epoch 230 - loss: 2.8960
lr 0.20000000 - epoch 231 - loss: 1.6833
lr 0.20000000 - epoch 232 - loss: 4.8111
lr 0.20000000 - epoch 233 - loss: 2.4010
lr 0.20000000 - epoch 234 - loss: 3.1682
lr 0.20000000 - epoch 235 - loss: 2.9292
lr 0.20000000 - epoch 236 - loss: 3.6763
lr 0.20000000 - epoch 237 - loss: 4.5642
lr 0.20000000 - epoch 238 - loss: 2.6453
lr 0.20000000 - epoch 239 - loss: 3.7629
lr 0.20000000 - epoch 240 - loss: 3.7744
lr 0.20000000 - epoch 241 - loss: 4.5673
lr 0.20000000 - epoch 242 - loss: 2.8136
lr 0.20000000 - epoch 243 - loss: 2.1635
lr 0.20000000 - epoch 244 - loss: 2.5895
lr 0.20000000 - epoch 245 - loss: 2.7291
lr 0.20000000 - epoch 246 - loss: 3.6283
lr 0.20000000 - epoch 247 - loss: 3.7361
lr 0.20000000 - epoch 248 - loss: 3.9418
lr 0.20000000 - 

...

lr 0.00500000 - epoch 1585 - loss: 0.7490
lr 0.00500000 - epoch 1586 - loss: 0.7039
lr 0.00500000 - epoch 1587 - loss: 0.6736
lr 0.00500000 - epoch 1588 - loss: 0.7275
lr 0.00500000 - epoch 1589 - loss: 0.8057
lr 0.00500000 - epoch 1590 - loss: 0.7024
lr 0.00500000 - epoch 1591 - loss: 0.7288
lr 0.00500000 - epoch 1592 - loss: 0.7268
lr 0.00500000 - epoch 1593 - loss: 0.7809
lr 0.00500000 - epoch 1594 - loss: 0.7340
lr 0.00500000 - epoch 1595 - loss: 0.7687
lr 0.00500000 - epoch 1596 - loss: 0.7042
lr 0.00500000 - epoch 1597 - loss: 0.7345
lr 0.00500000 - epoch 1598 - loss: 0.8463
lr 0.00500000 - epoch 1599 - loss: 0.7327
lr 0.00500000 - epoch 1600 - loss: 0.7923
lr 0.00500000 - epoch 1601 - loss: 0.7839
lr 0.00500000 - epoch 1602 - loss: 0.7431
lr 0.00500000 - epoch 1603 - loss: 0.8311
lr 0.00500000 - epoch 1604 - loss: 0.7639
lr 0.00500000 - epoch 1605 - loss: 0.8204
lr 0.00500000 - epoch 1606 - loss: 0.7222
lr 0.00500000 - epoch 1607 - loss: 0.8030
lr 0.00500000 - epoch 1608 - loss:

lr 0.00500000 - epoch 1781 - loss: 0.7475
lr 0.00500000 - epoch 1782 - loss: 0.8358
lr 0.00500000 - epoch 1783 - loss: 0.7918
lr 0.00500000 - epoch 1784 - loss: 0.7917
lr 0.00500000 - epoch 1785 - loss: 0.7654
lr 0.00500000 - epoch 1786 - loss: 0.7694
lr 0.00500000 - epoch 1787 - loss: 0.8310
lr 0.00500000 - epoch 1788 - loss: 0.8104
lr 0.00500000 - epoch 1789 - loss: 0.8259
lr 0.00500000 - epoch 1790 - loss: 0.7795
lr 0.00500000 - epoch 1791 - loss: 0.7389
lr 0.00500000 - epoch 1792 - loss: 0.7452
lr 0.00500000 - epoch 1793 - loss: 0.7727
lr 0.00500000 - epoch 1794 - loss: 0.8388
lr 0.00500000 - epoch 1795 - loss: 0.7432
lr 0.00500000 - epoch 1796 - loss: 0.7334
lr 0.00500000 - epoch 1797 - loss: 0.7781
lr 0.00500000 - epoch 1798 - loss: 0.7295
lr 0.00500000 - epoch 1799 - loss: 0.6958
lr 0.00500000 - epoch 1800 - loss: 0.8177
lr 0.00500000 - epoch 1801 - loss: 0.7365
lr 0.00500000 - epoch 1802 - loss: 0.7813
lr 0.00500000 - epoch 1803 - loss: 0.9272
lr 0.00500000 - epoch 1804 - loss:

lr 0.00500000 - epoch 1977 - loss: 0.9568
lr 0.00500000 - epoch 1978 - loss: 0.8281
lr 0.00500000 - epoch 1979 - loss: 0.7551
lr 0.00500000 - epoch 1980 - loss: 0.8103
lr 0.00500000 - epoch 1981 - loss: 0.7188
lr 0.00500000 - epoch 1982 - loss: 0.7539
lr 0.00500000 - epoch 1983 - loss: 0.7634
lr 0.00500000 - epoch 1984 - loss: 0.7564
lr 0.00500000 - epoch 1985 - loss: 0.7953
lr 0.00500000 - epoch 1986 - loss: 0.7212
lr 0.00500000 - epoch 1987 - loss: 0.8103
lr 0.00500000 - epoch 1988 - loss: 0.7293
lr 0.00500000 - epoch 1989 - loss: 0.7177
lr 0.00500000 - epoch 1990 - loss: 0.7398
lr 0.00500000 - epoch 1991 - loss: 0.7303
lr 0.00500000 - epoch 1992 - loss: 0.8077
lr 0.00500000 - epoch 1993 - loss: 0.7574
lr 0.00500000 - epoch 1994 - loss: 0.7064
lr 0.00500000 - epoch 1995 - loss: 0.7153
lr 0.00500000 - epoch 1996 - loss: 0.8222
lr 0.00500000 - epoch 1997 - loss: 0.7423
lr 0.00500000 - epoch 1998 - loss: 0.7862
lr 0.00500000 - epoch 1999 - loss: 0.8653
lr 0.00500000 - epoch 2000 - loss:

lr 0.00500000 - epoch 2174 - loss: 1.0246
lr 0.00500000 - epoch 2175 - loss: 0.8997
lr 0.00500000 - epoch 2176 - loss: 0.8364
lr 0.00500000 - epoch 2177 - loss: 0.8456
lr 0.00500000 - epoch 2178 - loss: 0.9021
lr 0.00500000 - epoch 2179 - loss: 0.8765
lr 0.00500000 - epoch 2180 - loss: 0.9111
lr 0.00500000 - epoch 2181 - loss: 0.7947
lr 0.00500000 - epoch 2182 - loss: 0.7412
lr 0.00500000 - epoch 2183 - loss: 0.7835
lr 0.00500000 - epoch 2184 - loss: 0.8298
lr 0.00500000 - epoch 2185 - loss: 0.8300
lr 0.00500000 - epoch 2186 - loss: 0.7271
lr 0.00500000 - epoch 2187 - loss: 0.7646
lr 0.00500000 - epoch 2188 - loss: 0.8150
lr 0.00500000 - epoch 2189 - loss: 0.8787
lr 0.00500000 - epoch 2190 - loss: 0.7753
lr 0.00500000 - epoch 2191 - loss: 0.7192
lr 0.00500000 - epoch 2192 - loss: 0.7315
lr 0.00500000 - epoch 2193 - loss: 0.7835
lr 0.00500000 - epoch 2194 - loss: 0.7841
lr 0.00500000 - epoch 2195 - loss: 0.8318
lr 0.00500000 - epoch 2196 - loss: 0.7696
lr 0.00500000 - epoch 2197 - loss:

lr 0.00500000 - epoch 2371 - loss: 0.7284
lr 0.00500000 - epoch 2372 - loss: 0.7780
lr 0.00500000 - epoch 2373 - loss: 0.8437
lr 0.00500000 - epoch 2374 - loss: 0.8638
lr 0.00500000 - epoch 2375 - loss: 0.7443
lr 0.00500000 - epoch 2376 - loss: 0.7151
lr 0.00500000 - epoch 2377 - loss: 0.7596
lr 0.00500000 - epoch 2378 - loss: 0.8771
lr 0.00500000 - epoch 2379 - loss: 0.7931
lr 0.00500000 - epoch 2380 - loss: 0.7795
lr 0.00500000 - epoch 2381 - loss: 0.7193
lr 0.00500000 - epoch 2382 - loss: 0.8463
lr 0.00500000 - epoch 2383 - loss: 0.7547
lr 0.00500000 - epoch 2384 - loss: 0.7743
lr 0.00500000 - epoch 2385 - loss: 0.7523
lr 0.00500000 - epoch 2386 - loss: 0.7702
lr 0.00500000 - epoch 2387 - loss: 0.7419
lr 0.00500000 - epoch 2388 - loss: 0.7638
lr 0.00500000 - epoch 2389 - loss: 0.8061
lr 0.00500000 - epoch 2390 - loss: 0.8412
lr 0.00500000 - epoch 2391 - loss: 0.7591
lr 0.00500000 - epoch 2392 - loss: 0.7830
lr 0.00500000 - epoch 2393 - loss: 0.8373
lr 0.00500000 - epoch 2394 - loss:

In [12]:
val_results
#2e-2

array([[2.43609667, 2.51898336, 2.63971066, 2.74202442, 2.47785997,
        2.64920545, 2.48485422, 2.63499951, 2.49928498, 2.42667556,
        2.59508038, 2.6920476 , 2.69270039, 2.47868419, 2.6673007 ,
        2.74025488]])